In [42]:
import pandas as pd

towns = pd.read_csv('data/communes-departement-region.csv')
towns['code_commune_INSEE'] = towns['code_commune_INSEE'].astype(str).str.zfill(5)
towns = towns.set_index('code_commune_INSEE')

town_headcounts = pd.read_excel('data/ensemble.xls', sheet_name='Communes', skiprows=7)
town_headcounts['code_commune_INSEE'] = (
    town_headcounts['Code département'].astype(str).str.zfill(2)
    .str.cat(
        town_headcounts['Code commune'].astype(str).str.zfill(3)
    )
)
town_headcounts = town_headcounts.set_index('code_commune_INSEE')
towns['headcount'] = town_headcounts['Population totale']
towns = towns.dropna(subset=['headcount'])
towns = towns.groupby(['nom_commune', 'latitude', 'longitude'])['headcount'].first()
towns = towns.reset_index().set_index('nom_commune')
towns.head()

latitude  longitude  headcount
nom_commune                                 
Aast         43.290877  -0.081773      182.0
Abainville   48.532698   5.515247      302.0
Abancourt    49.693055   1.769244      651.0
Abancourt    50.236870   3.207313      476.0
Abaucourt    48.892845   6.265597      309.0

In [63]:
import numpy as np

def distance(lat1, lon1, lat2, lon2):
    return (
        6367 * 2 * np.arcsin(np.sqrt(np.sin((np.radians(lat1) - np.radians(lat2))/2)**2 + np.cos(np.radians(lat2)) * np.cos(np.radians(lat1)) * np.sin((np.radians(lon1) - np.radians(lon2))/2)**2))
    )

toulouse = towns.loc['Toulouse']
leucate = towns.loc['Leucate']
eymoutiers = towns.loc['Eymoutiers']

candidates = towns.query('headcount >= 2000')
toulouse_distance = distance(candidates.latitude, candidates.longitude, toulouse.latitude, toulouse.longitude)
leucate_distance = distance(candidates.latitude, candidates.longitude, leucate.latitude, leucate.longitude)
eymoutiers_distance = distance(candidates.latitude, candidates.longitude, eymoutiers.latitude, eymoutiers.longitude)
candidates = candidates[
    (toulouse_distance < 150) &
    (leucate_distance < 150) &
    (eymoutiers_distance < 300)
]
candidates.head()

latitude  longitude  headcount
nom_commune                                 
Aiguefonde   43.492855   2.323156     2657.0
Albi         43.925821   2.146863    51567.0
Argeliers    43.311025   2.911155     2050.0
Arthès       43.963882   2.225870     2585.0
Aussillon    43.494682   2.355805     6283.0

In [65]:
for candidate in candidates.itertuples():
    break
candidate

Pandas(Index='Aiguefonde', latitude=43.4928550174, longitude=2.32315581418, headcount=2657.0)

In [66]:
import folium

france = folium.Map(
    location=[46.2276, 2.2137],
    zoom_start=6,
    tiles='Stamen Terrain'
)

with open('data/formes-des-lignes-du-rfn.geojson') as f:
    railways = json.load(f)
    railways['features'] = [
        rw for rw in railways['features']
        if rw['properties']['libelle'] == 'Exploitée'
    ]
    folium.GeoJson(railways, name="geojson").add_to(france)

for home in [toulouse, leucate, eymoutiers]:
    folium.Marker(
        [home.latitude, home.longitude],
        tooltip=home.name,
        icon=folium.Icon(color="green")
    ).add_to(france)

for candidate in candidates.itertuples():
    folium.Circle(
        radius=100,
        location=[candidate.latitude, candidate.longitude],
        tooltip=candidate.Index,
        color="crimson",
        fill=False,
    ).add_to(france)

france

In [67]:
france.save("map.html")